# NCATS Translator Workflow 5, Modules 1-4 - Red Team (COHD)
## Gender-related conditions
This is a Red Team implementation of NCATS Translator Workflow 5, Modules 1-4 using COHD to find conditions more prevalent in women than in men and vice versa.

In [1]:
import pandas as pd
import numpy as np
from cohd_requests import *
from cohd_utilities import *

### Display settings (optional)

In [2]:
# Pandas display options
pd.options.display.max_colwidth = 255
pd.options.display.max_rows = None

# Wider notebook display
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

## 1) Using the 5-year non-hierarchical data set

In [3]:
dataset_id = 3

## 2) Define male and female cohorts

In [4]:
concept_female = 8532
concept_male = 8507
domain = 'Condition'  # This can be changed to 'Drug' or 'Procedure' to find concepts in those domains instead

## 3) Get conditions associated with each gender

In [5]:
df_association_female = obs_exp_ratio(concept_female, concept_id_2=None, domain_id=domain, dataset_id=dataset_id)
df_association_male = obs_exp_ratio(concept_male, concept_id_2=None, domain_id=domain, dataset_id=dataset_id)

## 4) Filter the list of associated conditions

### 4.1) Exclude gender-specific conditions from list of associated conditions.
Many of the enhanced conditions in each gender are just conditions that do not occur in the opposite gender. Do this by comparing the single concept prevalences with the co-occurrence rate. If the co-occurrence rate is much less than the expected co-occurrence rate for independence (or doesn't appear in the data), then exclude that concept from the list

In [6]:
# Get the prevalences for male and female
df_gender_prev = concept_frequency([concept_female, concept_male], dataset_id=dataset_id)

# Pull out the prevalences
prev_female = df_gender_prev[df_gender_prev['concept_id']==concept_female]['concept_frequency'].iloc[0]
prev_male = df_gender_prev[df_gender_prev['concept_id']==concept_male]['concept_frequency'].iloc[0]

# Get single concept prevalences for all concepts
df_conditions = most_frequent_concepts(limit=1000000, dataset_id=dataset_id, domain_id=domain)

# Set the index to the appropriate concept IDs for join operation
df_conditions = df_conditions.set_index('concept_id')
df_association_female = df_association_female.set_index('concept_id_2')
df_association_male = df_association_male.set_index('concept_id_2')

# Exctract certain columns and rename for join operation
df_association_female_join = df_association_female[['observed_count']].rename(columns={'observed_count': 'observed_count_female'})
df_association_male_join = df_association_male[['observed_count']].rename(columns={'observed_count': 'observed_count_male'})

# Left-join co-occurrence table with single
df_joined = df_conditions.join([df_association_female_join, df_association_male_join], how='left')

# Find (potentially) gender-specific concepts by finding concepts where the observed gender-concept co-occurrence is much smaller than the expected gender-concept co-occurrence
# Note that when co-occurrences are <= 10, they do not appear in the COHD data, hence we will exclude all concepts that have a gender-concept co-occurrence <= 10.
def gender_specific(row):
    threshold = 10
    return np.isnan(row['observed_count_female']) or \
        (row['observed_count_female'] < (row['concept_count'] * prev_female / threshold)) or \
        np.isnan(row['observed_count_male']) or \
        (row['observed_count_male'] < (row['concept_count'] * prev_male / threshold))
    
df_joined['gender_specific'] = df_joined.apply(gender_specific, axis=1)
df_gender_specific = df_joined[['gender_specific']]

# Show the concepts detected as gender specific
display(df_joined[df_joined.gender_specific])

# Remove gender-specific concepts from the associations
df_association_female_filtered = df_association_female.join(df_gender_specific, how='left')
df_association_female_filtered = df_association_female[~df_association_female_filtered['gender_specific']]
df_association_male_filtered = df_association_male.join(df_gender_specific, how='left')
df_association_male_filtered = df_association_male[~df_association_male_filtered['gender_specific']]

concept_class_id  concept_count  concept_frequency  \
concept_id                                                           
4095793         Clinical Finding         151396           0.087418   
4180154         Clinical Finding         118427           0.068381   
37102309                    HLGT         109563           0.063263   
37103738                     HLT         107572           0.062114   
443343          Clinical Finding         104781           0.060502   
200452          Clinical Finding         103102           0.059533   
4090861         Clinical Finding          72916           0.042103   
4181194         Clinical Finding          72294           0.041744   
196738          Clinical Finding          71303           0.041171   
4124486         Clinical Finding          70473           0.040692   
37103733                     HLT          61128           0.035296   
200780          Clinical Finding          60048           0.034673   
4115107         Clinical Finding          56399           0.032566   
4040738         Clinical Finding          46458           0.026826   
36602225                    HLGT          46447           0.026819   
4088777         Clinical Finding          46426           0.026807   
36302163                    HLGT          46071           0.026602   
4024004         Clinical Finding          45684           0.026379   
4095475         Clinical Finding          44832           0.025887   
36303119                     HLT          43996           0.025404   
4127688         Clinical Finding          43482           0.025107   
37102304                    HLGT          42691           0.024650   
37103720                     HLT          42241           0.024391   
196734          Clinical Finding          42138           0.024331   
4093344         Clinical Finding          42107           0.024313   
37102301                    HLGT          41712           0.024085   
4128492         Clinical Finding          41362           0.023883   
4190189         Clinical Finding          41033           0.023693   
4190186         Clinical Finding          40777           0.023545   
37103719                     HLT          40301           0.023270   
37103734                     HLT          39363           0.022729   
36603383                     HLT          39280           0.022681   
36602226                    HLGT          39211           0.022641   
439658          Clinical Finding          38792           0.022399   
45757399        Clinical Finding          38553           0.022261   
4131756         Clinical Finding          38437           0.022194   
37102297                    HLGT          37884           0.021875   
193254          Clinical Finding          36352           0.020990   
4131007         Clinical Finding          33889           0.019568   
80767           Clinical Finding          33405           0.019289   
37103702                     HLT          32086           0.018527   
35502621                     HLT          31093           0.017954   
36603394                     HLT          31018           0.017910   
36602228                    HLGT          30828           0.017801   
197032          Clinical Finding          29630           0.017109   
37103688                     HLT          29621           0.017104   
198803          Clinical Finding          29335           0.016938   
40483613        Clinical Finding          29275           0.016904   
36603376                     HLT          28197           0.016281   
4113639         Clinical Finding          28127           0.016241   
36603375                     HLT          27410           0.015827   
201817          Clinical Finding          27115           0.015657   
37103714                     HLT          26835           0.015495   
37102303                    HLGT          26482           0.015291   
37102302                    HLGT          26436           0.015265   
4299535         Clinical F

## 5) Calculate the ratio of prevalence between genders
Add columns with ratio between genders for easier interpretation

In [7]:
# Join
df_sex = df_association_female_filtered.join(df_association_male_filtered[['concept_id_1', 'observed_count', 'expected_count', 'ln_ratio']], how='inner', lsuffix='_female', rsuffix='_male')

# Calculate the ratio between the ln_ratios of asthma and severe asthma
# subtraction of ln_ratios should be same as division of the ratios
df_sex['ln_ratio_female_vs_male'] = (df_sex.ln_ratio_female - df_sex.ln_ratio_male)

# Calculate 99.9% confidence intervals from Poisson distribution
df_sex[['ci_female', 'ci_male', 'significant']] = \
    df_sex.apply(PoissonSignificance2, axis=1, result_type='expand', c_oc1='observed_count_female', c_oc2='observed_count_male',
                 c_lr1='ln_ratio_female', c_lr2='ln_ratio_male', interval=0.999)

D:\NCATS\translator-workflows\Workflow5\cohd\cohd_utilities.py:9: RuntimeWarning: divide by zero encountered in log
  return np.log(PoissonConfInt(rate, interval, iterations) * np.exp(ln_ratio) / rate)


### Female
Showing the top 1000 conditions more prevalent in females

In [8]:
# Display the most drastic significant conditions that are more prevalent in females
display(df_sex[df_sex.significant].sort_values(by='ln_ratio_female_vs_male', ascending=False).head(1000))

dataset_id  concept_id_1_female  \
concept_id_2                                    
37303826               3                 8532   
37103692               3                 8532   
36102962               3                 8532   
4128846                3                 8532   
37102294               3                 8532   
4022933                3                 8532   
432375                 3                 8532   
37103689               3                 8532   
4124325                3                 8532   
40479565               3                 8532   
195007                 3                 8532   
4148914                3                 8532   
4202515                3                 8532   
77030                  3                 8532   
4035976                3                 8532   
37604047               3                 8532   
434484                 3                 8532   
72578                  3                 8532   
4028865                3                 8532   
4242498                3                 8532   
4021344                3                 8532   
40405599               3                 8532   
441077                 3                 8532   
80951                  3                 8532   
4275488                3                 8532   
36603386               3                 8532   
36302173               3                 8532   
4146239                3                 8532   
4085075                3                 8532   
4141878                3                 8532   
444461                 3                 8532   
436675                 3                 8532   
198984                 3                 8532   
4011628                3                 8532   
4265765                3                 8532   
36802260               3                 8532   
4013540                3                 8532   
36603382               3                 8532   
4264234                3                 8532   
4081086                3                 8532   
4080995                3                 8532   
4095779                3                 8532   
4214550                3                 8532   
4038490                3                 8532   
4130532                3                 8532   
4021650                3                 8532   
43020429               3                 8532   
4248870                3                 8532   
4047650                3                 8532   
4052837                3                 8532   
4022231                3                 8532   
4106092                3                 8532   
434298                 3                 8532   
4031159                3                 8532   
40486024               3                 8532   
4128194                3                 8532   
4119432                3                 8532   
443415                 3                 8532   
4314073                3                 8532   
4177244                3                 8532   
4300305                3                 8532   
36403208               3                 8532   
4119189                3                 8532   
4216341                3                 8532   
443524                 3                 8532   
4095786                3                 8532   
45885339               3                 8532   
43562815               3                 8532   
4129213                3                 8532   
4029434                3                 8532   
140173                 3                 8532   
438407                 3                 8532   
4165545                3                 8532   
137520                 3                 8532   
4113104                3                 8532   
377527                 3                 8532   
36303162               3                 8532   
4185187                3                 8532   
37103708               3                 8532   
4198803                3                 8532

### Male
Showing the top 1000 conditions more prevalent in males

In [9]:
# Display the most drastic significant conditions that are more prevalent in females
display(df_sex[df_sex.significant].sort_values(by='ln_ratio_female_vs_male', ascending=True).head(1000))

dataset_id  concept_id_1_female  \
concept_id_2                                    
43053699               3                 8532   
36903641               3                 8532   
201792                 3                 8532   
37102299               3                 8532   
77673                  3                 8532   
199859                 3                 8532   
4167100                3                 8532   
197919                 3                 8532   
195926                 3                 8532   
4156664                3                 8532   
433410                 3                 8532   
4167354                3                 8532   
4225244                3                 8532   
40492320               3                 8532   
4015218                3                 8532   
36903646               3                 8532   
200450                 3                 8532   
4295624                3                 8532   
4091342                3                 8532   
197023                 3                 8532   
4012231                3                 8532   
201951                 3                 8532   
4341084                3                 8532   
440988                 3                 8532   
4181828                3                 8532   
4340511                3                 8532   
37604037               3                 8532   
4117242                3                 8532   
36902282               3                 8532   
4025663                3                 8532   
4117404                3                 8532   
437700                 3                 8532   
4247350                3                 8532   
443709                 3                 8532   
4101067                3                 8532   
136916                 3                 8532   
43530625               3                 8532   
4182140                3                 8532   
4129082                3                 8532   
443232                 3                 8532   
4188441                3                 8532   
4092379                3                 8532   
4222781                3                 8532   
4090872                3                 8532   
201688                 3                 8532   
4209905                3                 8532   
4092059                3                 8532   
4041276                3                 8532   
4092885                3                 8532   
35702713               3                 8532   
433813                 3                 8532   
440345                 3                 8532   
44783857               3                 8532   
4288544                3                 8532   
4126274                3                 8532   
4341635                3                 8532   
4096008                3                 8532   
194475                 3                 8532   
432838                 3                 8532   
37003681               3                 8532   
4095598                3                 8532   
195590                 3                 8532   
4220328                3                 8532   
379157                 3                 8532   
4181332                3                 8532   
4081041                3                 8532   
4032438                3                 8532   
195864                 3                 8532   
376555                 3                 8532   
37103705               3                 8532   
79198                  3                 8532   
434176                 3                 8532   
35302076               3                 8532   
195862                 3                 8532   
4042409                3                 8532   
440068                 3                 8532   
434252                 3                 8532   
4210147                3                 8532   
4182431                3                 8532   
444056                 3                 8532

## 6) Get drugs associated with each gender

In [11]:
df_association_female = obs_exp_ratio(concept_female, concept_id_2=None, domain_id=domain, dataset_id=dataset_id)
df_association_male = obs_exp_ratio(concept_male, concept_id_2=None, domain_id=domain, dataset_id=dataset_id)

## 7) Compare ln_ratios between conditions associated with asthma vs severe asthma

In [12]:
# Join
df_sex = df_association_female_filtered.join(df_association_male_filtered[['concept_id_1', 'observed_count', 'expected_count', 'ln_ratio']], how='inner', lsuffix='_female', rsuffix='_male')

# Calculate the ratio between the ln_ratios of asthma and severe asthma
# subtraction of ln_ratios should be same as division of the ratios
df_sex['ln_ratio_female_vs_male'] = (df_sex.ln_ratio_female - df_sex.ln_ratio_male)

# Calculate 99.9% confidence intervals from Poisson distribution
df_sex[['ci_female', 'ci_male', 'significant']] = \
    df_sex.apply(PoissonSignificance2, axis=1, result_type='expand', c_oc1='observed_count_female', c_oc2='observed_count_male',
                 c_lr1='ln_ratio_female', c_lr2='ln_ratio_male', interval=0.999)

D:\NCATS\translator-workflows\Workflow5\cohd\cohd_utilities.py:9: RuntimeWarning: divide by zero encountered in log
  return np.log(PoissonConfInt(rate, interval, iterations) * np.exp(ln_ratio) / rate)


### Female
Showing the top 1000 conditions more prevalent in females

In [ ]:
# Display the most drastic significant conditions that are more prevalent in females
display(df_sex[df_sex.significant].sort_values(by='ln_ratio_female_vs_male', ascending=False).head(1000))

### Male
Showing the top 1000 conditions more prevalent in males

In [ ]:
# Display the most drastic significant conditions that are more prevalent in females
display(df_sex[df_sex.significant].sort_values(by='ln_ratio_female_vs_male', ascending=True).head(1000))